# OpenStreetMap - A Data Cleaning Case Study

# Cleaning [OpenStreetMap](http://www.openstreetmap.org/) Data

If you're wondering what OpenStreetMap is, think of it as Wikipedia but for meta-data-filled maps of the world. I would argue that it's one of the most important technologies you've probably never heard of. From the [OpenStreetMap Wiki](https://wiki.openstreetmap.org/wiki/Main_Page):

> "Welcome to OpenStreetMap, the project that creates and distributes free geographic data for the world. We started it because most maps you think of as free actually have legal or technical restrictions on their use, holding back people from using them in creative, productive, or unexpected ways."

If you're like me and you're refining your XML parsing/Python scripting/SQL querying skills, why not use said skills to clean some OpenStreetMap data? I'm going to be as detailed as possible below so anyone interested can follow along as an exercise. 

According to [The New York Times' 'What Could Disappear'](http://www.nytimes.com/interactive/2012/11/24/opinion/sunday/what-could-disappear.html?_r=2&) interactive article, New Orleans could be 88% below sea level in as little as 100 years. I'm personally interested to see what we're set to lose as a consequence of global warming so I'll focus on approximately 100x150 mile area [surrounding New Orleans](https://mapzen.com/data/metro-extracts/metro/new-orleans_louisiana/).

___

### Getting to know the data:
OpenStreetMap data is available as XML bearing the file type '.osm'. Reading through the [documentation](https://wiki.openstreetmap.org/wiki/Main_Page), the gist of the main components of a osm file is:
* a **'node'** element essentially represents a latitude/longitude coordinate. It may have 'tag' child elements with other data points comprising things like an 'address ' or features such as 'school'.
* a **'way'** element has nodes as children(with their element type shortened to 'nd'). It defines things like roads, buildings, natural areas, etc. Also may have 'tag' children for the same purpose as a node.
* a **'relation'** has nested 'member' elements which reference existing ways and nodes. It defines relationships among the other elements such as an extended hiking trail made up by a number of way elements.

The osm file unzips to a whopping 1.28gb and crashes both Atom and SublimeText on my machine. [VIM](http://www.vim.org/), on the other hand, is a text editor designed to be used in a bare-bones command line interface (like the Terminal app on a mac) that can easily handle the job, allowing me to jump around and explore freely. Some VIM commands that let me do this are:
* Jump to bottom: `shift+g`
* Jump to top: `gg`
* page down: `Control+d`
* page up: `Control+u`
* Jump five million lines down: type `5000000` and then hit `j`
* Jump five million lines up: type `5000000` and then hit `k`
* Search the entire massive file for anything you want: type `/` followed by your search
* Go to the next instance of what you searched for: `n`
    
*Check out [this little gem](https://vim-adventures.com/) to get started with VIM in a fun way.*

Here is what I learned from exploring the file:
* the file has the standard opening:  <?xml version='1.0' encoding='UTF-8'?>
* the XML root element is 'osm' and is parent to all other elements
* there are 16,082,009 lines in total - wow!
* an example of a node element with no tags:

![node](supporting_files/screenshots/node.png "node")

* a node element with tags:

![node with tags](supporting_files/screenshots/node_tags.png "node with tags")

* a way element with its nested nd (node) element references and tags:

![way](supporting_files/screenshots/way.png "way")

* a relation element with its nested nodes, ways and tags:

![relation](supporting_files/screenshots/relation.png "relation")

### Reflecting upon the data - what should I clean?:
'tag' elements seem to constitute the bulk of a 'way' or 'relation' element's meta-data. From what I understand about OpenStreetMap, this should also be where a lot of user-generated/added content is stored. I'm sure there will be cleaning to do there. One other thing catches my eye - the large number of 'tag' elements who's 'k' attribute contains the acronym 'NHD'. What is that about?

It turns out NHD is an acronym for the US Geological Survey's ['National Hydrography Dataset'](https://nhd.usgs.gov/) which maps out and documents the nation's watershed boundaries and their features. New Orleans is surrounded by a massive amount of such natural features:


![new orleans watershed](supporting_files/screenshots/new_orleans_watershet.png "new orleans watershed")


I would assume the data to be damn near perfect given it was most likely adopted directly from the NHD. The wonderful thing here is that, without much trouble, I can programmatically verify whether or not that is true despite the over 16 million lines of data to deal with. This could be another opportunity for data cleaning.

Here we go!!!

### Auditing the data:
Looking again at the sample 'way' and 'relation' elements in the 'Getting to know the data:' section above, 'NHD' stands out as a prefix for the field names of the NHD data (ex. 'ComID', 'FCode' and 'FTYPE'). 'FTYPE' appears to define a type of natural feature, which in the case of our examples is a stream/river or a swamp/marsh. This is exactly what I'm interested in for my cleaning so I'm going to leverage it to isolate the 'node', 'way' or 'relation' elements I want and have a look at all the possible keys: 

In [1]:
import xml.etree.ElementTree as ET

OSM_FILE = "/Users/mchana/GitHub/udacity/large_files/new-orleans_region.osm"

def count_elem(osm_file, tags=('node', 'way', 'relation')):
    tag_set = set() 
    
    context = ET.iterparse(osm_file, events=('start', 'end'))
    _, root = next(context)
    
    for event, elem in context:
        if event == 'end' and elem.tag in tags:
            for tag_elem in elem.iter("tag"):
                if tag_elem.attrib['k'] == 'NHD:ComID':
                    for tag_elem in elem.iter("tag"):
                        tag_set.add(tag_elem.attrib['k'])
        root.clear()
    return tag_set

keys_list = list(count_elem(OSM_FILE))
sorted(keys_list)

['NHD:ComID',
 'NHD:Elevation',
 'NHD:FCode',
 'NHD:FDate',
 'NHD:FTYPE',
 'NHD:FType',
 'NHD:GNIS_ID',
 'NHD:GNIS_Name',
 'NHD:Permanent_',
 'NHD:RESOLUTION',
 'NHD:ReachCode',
 'NHD:Resolution',
 'NHD:way_id',
 'admin_level',
 'attribution',
 'boat',
 'boundary',
 'created_by',
 'culvert',
 'ele',
 'gnis:county_id',
 'gnis:created',
 'gnis:feature_id',
 'gnis:state_id',
 'history',
 'landuse',
 'layer',
 'leisure',
 'lock',
 'man_made',
 'name',
 'natural',
 'note',
 'place',
 'source',
 'tunnel',
 'type',
 'water',
 'waterway',
 'wetland']

Looking over the list I can already see some possible redundancies in the field naming convention for some of the NHD keys. I can reference these field names against the official [NHD data model](https://nhd.usgs.gov/NHDv2.2.1_poster_081216.pdf) (last updated on August 1st 2016) and [NHD data dictionary](https://nhd.usgs.gov/userGuide/Robohelpfiles/NHD_User_Guide/Feature_Catalog/Data_Dictionary/Data_Dictionary.htm) in order to clarify. I'll investigate the validity of each one and note here those that I find problematic or noteworthy:

##### NHD:ComID:
The 'Model Changes' section of the NHD data model notes, "ComID field deleted from all feature classes/tables". This field has been replaced by one called 'Permanent_Identifier', yet it is still valid as the NHD data dictionary clarifies - "features already assigned a ComID retain that value as the Permanent_ Identifier". While this is an important note for future data entry, it will not require cleaning here.

##### NHD:FTYPE and NHD:FType
Manually searching through my osm file with VIM (ex. `/NHD:FTYPE`) reveals that both 'FTYPE' and 'FType' are referring to the same category of things - 'SwampMarsh', 'StreamRiver', etc. It's pretty clear they can be united into a single field name, which is according to the NHD data model should be 'FType'. 

##### NHD:GNIS_ID
'GNIS' stands for the '[Geographic Names Information System](https://nhd.usgs.gov/gnis.html)', which is another data set from the U.S. Geological Survey:

>"The Geographic Names Information System (GNIS), developed by the U.S. Geological Survey in cooperation with the U.S. Board on Geographic Names, contains information about physical and cultural geographic features in the United States and associated areas..."

Each instance of 'NHD:GNIS_ID' that I find in the osm file seems to be followed by another 'tag' element containing the key 'gnis:feature_id' that bears the exact same numbers as its value. It's fair to say that this is redundant data. Because this is data removal, the best i can do here is to point out the pairs so that OpenStreetMap can remove the data should they choose. I'll do this via SQL queries later in this case study.

##### NHD:Permanent_
When i manually examine the osm file searching for the key I find that it's not a "40-char GUID value that uniquely identifies the occurrence of each feature in The National Map. National Database primary key." as stated in the NHD Data Model dictionary. In fact, if I look again at the other 'tag' elements I can see that the same value is repeated in the 'NHD:ComID' tag element. I can find elements with duplicate values for NHD:ComID and NHD:Permanent_ using SQL later in this case study.

##### NHD:RESOLUTION
Just as 'NHD:FTYPE' is redundant with 'NHD:FType', 'NHD:RESOLUTION' is redundant with 'NHD:Resolution'. 

#### NHD:way_id
Just as 'NHD:Permanent_' bears the same value as 'NHD:ComID', so does 'NHD:way_id'. There is something going on here. Also, 'way_id' is not an official feature of the NHD data model. I'll do an SQL query to show where it it duplicated with COMID and can be removed:

Onto the remaining fields, there isn't an official source I can verify they are structurally correct or what data they correspond to. So I'll just print out each one with a list of all the unique values they correspond to from the osm file:

In [2]:
import xml.etree.ElementTree as ET
import collections as col
import pprint

OSM_FILE = "/Users/mchana/GitHub/udacity/large_files/new-orleans_region.osm"

def make_elem_dict(osm_file, tags=('node', 'way', 'relation')):
    
    elem_dict = col.defaultdict(set)
    
    context = ET.iterparse(osm_file, events=('start', 'end'))
    _, root = next(context)
    
    # opportunity for 'continue' here...
    # also, pull out - make function to find correct element
    for event, elem in context:
        if event == 'end' and elem.tag in tags:
            for tag in elem.iter("tag"):
                if tag.attrib['k'] == 'NHD:ComID':
                    # am overwriting tag here from prev. loop - call something else
                    for tag in elem.iter("tag"):
                        elem_dict[tag.attrib['k']].add(tag.attrib['v'])
        root.clear()
    return elem_dict

pprint.pprint(make_elem_dict(OSM_FILE))

defaultdict(<class 'set'>,
            {'NHD:ComID': {'121369572',
                           '121376748',
                           '121376910',
                           '121376927',
                           '121379126',
                           '131339718',
                           '131339719',
                           '131339720',
                           '131339721',
                           '133385498',
                           '137031874',
                           '137032010',
                           '137032289',
                           '137032340',
                           '139142583',
                           '139142584',
                           '139142585',
                           '139142586',
                           '139142587',
                           '139142588',
                           '139142590',
                           '139142591',
                           '139142595',
                           '139142597',
             

                           '139145348',
                           '139145350',
                           '139145352',
                           '139145354',
                           '139145355',
                           '139145358',
                           '139145359',
                           '139145361',
                           '139145364',
                           '139145365',
                           '139145366',
                           '139145367',
                           '139145369',
                           '139145370',
                           '139145372',
                           '139145375',
                           '139145376',
                           '139145377',
                           '139145378',
                           '139145379',
                           '139145381',
                           '139145382',
                           '139145386',
                           '139145387',
                           '139145389',


                           '139147884',
                           '139147887',
                           '139147888',
                           '139147890',
                           '139147891',
                           '139147892',
                           '139147893',
                           '139147894',
                           '139147897',
                           '139147898',
                           '139147899',
                           '139147900',
                           '139147901',
                           '139147902',
                           '139147903',
                           '139147905',
                           '139147907',
                           '139147909',
                           '139147910',
                           '139147911',
                           '139147912',
                           '139147914',
                           '139147916',
                           '139147917',
                           '139147918',


                           '139151903',
                           '139151905',
                           '139151906',
                           '139151907',
                           '139151908',
                           '139151909',
                           '139151911',
                           '139151912',
                           '139151913',
                           '139151914',
                           '139151915',
                           '139151917',
                           '139151918',
                           '139151919',
                           '139151920',
                           '139151921',
                           '139151922',
                           '139151923',
                           '139151924',
                           '139151925',
                           '139151926',
                           '139151927',
                           '139151929',
                           '139151930',
                           '139151932',


                           '139155779',
                           '139155780',
                           '139155781',
                           '139155782',
                           '139155784',
                           '139155786',
                           '139155787',
                           '139155788',
                           '139155789',
                           '139155790',
                           '139155791',
                           '139155792',
                           '139155793',
                           '139155799',
                           '139155801',
                           '139155802',
                           '139155803',
                           '139155804',
                           '139155806',
                           '139155807',
                           '139155808',
                           '139155809',
                           '139155810',
                           '139155811',
                           '139155813',


...

                            '139148174',
                            '139148175',
                            '139148176',
                            '139148177',
                            '139148179',
                            '139148181',
                            '139148184',
                            '139148185',
                            '139148187',
                            '139148188',
                            '139148189',
                            '139148190',
                            '139148191',
                            '139148194',
                            '139148196',
                            '139148197',
                            '139148198',
                            '139148199',
                            '139148200',
                            '139148201',
                            '139148202',
                            '139148204',
                            '139148205',
                            '139148207',
                

                            '139151889',
                            '139151890',
                            '139151892',
                            '139151894',
                            '139151897',
                            '139151899',
                            '139151901',
                            '139151903',
                            '139151905',
                            '139151906',
                            '139151907',
                            '139151908',
                            '139151909',
                            '139151911',
                            '139151912',
                            '139151913',
                            '139151914',
                            '139151915',
                            '139151917',
                            '139151918',
                            '139151919',
                            '139151920',
                            '139151921',
                            '139151922',
                

                            '139155663',
                            '139155664',
                            '139155665',
                            '139155666',
                            '139155668',
                            '139155671',
                            '139155672',
                            '139155673',
                            '139155674',
                            '139155675',
                            '139155676',
                            '139155678',
                            '139155680',
                            '139155681',
                            '139155682',
                            '139155684',
                            '139155685',
                            '139155688',
                            '139155691',
                            '139155692',
                            '139155693',
                            '139155694',
                            '139155695',
                            '139155698',
                

                            '148744168',
                            '148744169',
                            '148744170',
                            '148744171',
                            '148744172',
                            '148744173',
                            '148744174',
                            '148744175',
                            '148744176',
                            '148744177',
                            '148744178',
                            '148744179',
                            '148744180',
                            '148744181',
                            '148744182',
                            '148744183',
                            '148744184',
                            '148744185',
                            '148744186',
                            '148744187',
                            '148744188',
                            '148744189',
                            '148744190',
                            '148744191',
                

                                 '00556228',
                                 '00556414',
                                 '00556441',
                                 '00556548',
                                 '00558149',
                                 '00558153',
                                 '00558225',
                                 '00558306',
                                 '00558625',
                                 '00558682',
                                 '00558710',
                                 '00558722',
                                 '00558730',
                                 '00558765',
                                 '00559628',
                                 '00559695',
                                 '00559711',
                                 '00559750',
                                 '00559752',
                                 '00559823',
                                 '00559851',
                                 '00559853',
          

Starting from the top of the list, the standouts are:

##### NHD:ComID
It has more than one entry in some of them. I track down way 43261226, but nothing I can do here reallly.

##### NHD:FCode
Again, more than one entry, but this seems ok to have more than one. 


##### NHD:FDate
Dupes, nothing can do

##### NHD:FTYPE and FHD:FType
Will be merged 

##### NHD:ReachCode
* "Unique identifier composed of two parts, first eight digits = subbasin code as defined by FIPS 103, and next six digits = random-assigned sequential number unique within a Cataloguing Unit."
    * issues that I see but can't fix:
           * Is supposed to be a unique identifier but some have more than one. Manually inspecting one such element doesn't reveal why, but noticed also has two NHD:ComID values. (WayID: 43393226)
           
##### NHD:way_id 
not official, dupe of other data

##### name
Scanning through 'name' I can see there is just an inconsistency in the naming, where some have the first letter of each capitalized and others don't. I'll fix that.

##### natural
There appears to be a redundant value between '_coastline' and 'coastline'. A quick VIM search in the osm document for '_coastline' reveals a 'note' key in a 'tag' element reading "I have altered the natural:coatline tag as this way duplicates existing coastline ways". Not touching this one.

##### note
I'm not really sure what this is about so I'll write a little script to pull out all elements bearing a 'note' tag element to inspect:



In [3]:
import xml.etree.ElementTree as ET

OSM_FILE = "/Users/mchana/GitHub/udacity/large_files/new-orleans_region.osm"

def find_note_tag(osm_file):
    context = ET.iterparse(osm_file, events=('start', 'end'))
    _, root = next(context)
    
    for event, elem in context:
        if event == 'end' and (elem.tag == 'node' or elem.tag == 'way' or elem.tag == 'relation'):
            for tag_elem in elem.iter("tag"):
                if tag_elem.attrib['k'] == 'NHD:ComID':
                    for tag_elem in elem.iter("tag"):
                        if tag_elem.attrib['k'] == 'note':
                            print(ET.dump(elem))
        root.clear()
find_note_tag(OSM_FILE)

<way changeset="12512084" id="46179177" timestamp="2012-07-27T14:15:07Z" uid="22925" user="ELadner" version="9">
		<nd ref="549574941" />
		<nd ref="549574939" />
		<nd ref="1122849628" />
		<nd ref="1121382828" />
		<nd ref="549574933" />
		<nd ref="1121161585" />
		<nd ref="549574926" />
		<nd ref="549574925" />
		<nd ref="549574922" />
		<nd ref="549574921" />
		<nd ref="1122910760" />
		<nd ref="1121424207" />
		<nd ref="1120689016" />
		<nd ref="1120757160" />
		<nd ref="549574913" />
		<nd ref="1121246452" />
		<nd ref="549574906" />
		<nd ref="549574904" />
		<nd ref="549574902" />
		<nd ref="549574900" />
		<nd ref="549574898" />
		<nd ref="549574649" />
		<nd ref="549574647" />
		<nd ref="549574646" />
		<nd ref="1122150873" />
		<nd ref="1120558234" />
		<nd ref="549574642" />
		<nd ref="1121289595" />
		<nd ref="549574639" />
		<nd ref="549574638" />
		<nd ref="549574637" />
		<nd ref="549574636" />
		<nd ref="1120666323" />
		<nd ref="549574633" />
		<nd ref="549574632" />


		<tag k="NHD:FCode" v="44500" />
		<tag k="NHD:FDate" v="2009/01/15" />
		<tag k="NHD:FTYPE" v="SeaOcean" />
		<tag k="NHD:RESOLUTION" v="High" />
	</way>
	
None
<way changeset="12506377" id="173109934" timestamp="2012-07-27T03:21:58Z" uid="22925" user="ELadner" version="1">
		<nd ref="549575326" />
		<nd ref="1839421429" />
		<nd ref="1839421436" />
		<nd ref="1839421434" />
		<nd ref="1839421433" />
		<nd ref="1839421438" />
		<nd ref="1839421441" />
		<nd ref="1839421428" />
		<nd ref="1839421412" />
		<nd ref="1839421410" />
		<nd ref="1839421406" />
		<nd ref="1839421401" />
		<nd ref="1839421399" />
		<nd ref="1839421396" />
		<nd ref="1839421392" />
		<nd ref="1839421388" />
		<nd ref="1839421386" />
		<nd ref="1839421385" />
		<nd ref="1839421381" />
		<nd ref="1839421380" />
		<nd ref="1839421362" />
		<nd ref="1839421360" />
		<nd ref="1839421354" />
		<nd ref="1839421356" />
		<nd ref="1839421333" />
		<nd ref="1839421330" />
		<nd ref="1839421320" />
		<nd ref="1839421312"

Not going to do anything about the parent or 'tag' child elements with 'note' as their key.

##### source
Fix, NHD & bing to NHD & Bing

##### water
Minor, but Bayou should be bayou.

### Parse, clean and compile database:

run data.py

So now that I've noted above how to fix each thing, here is how I'm going to do it (algos)

Next, here is how the data will be parsed, cleaning algos inserted, and database compiled (algo)

### Examine the data efficiently with database queries

First I build the database:

In [4]:
import sqlite3
import csv
from pprint import pprint
from supporting_files import database_schema as ds
import os

sqlite_file = 'supporting_files/exports_databases/osm_db.db'
conn = sqlite3.connect(sqlite_file)
c = conn.cursor()

In [5]:
sql_schema = ds.sql_schema

In [6]:
# Create the table, specifying the schema
c.executescript(sql_schema)
# commit the changes
conn.commit()

In [7]:
# first row of CSVs MUST be fieldnames
import os
from csv import DictReader

def add_table_from_csv(filename):
    if not filename.endswith('.csv'):
        return
    
    tablename = filename.split(".")[0].split('/')[-1]
    with open(filename, 'r') as fin:
        dr = DictReader(fin)
        fieldnames = dr.fieldnames
        to_db = [tuple( [i[k] for k in dr.fieldnames] ) for i in dr]
    c.executemany("INSERT INTO {}({}) VALUES({}?);".format(
            tablename, ",".join(dr.fieldnames), "?," * (len(dr.fieldnames)-1)), to_db)
    conn.commit()
    
def add_to_db(directory):
    for f_name in os.listdir(directory):
        full_path = os.path.join(directory, f_name)
        add_table_from_csv(full_path)

add_to_db('supporting_files/exports')

##### Investigate any other questions I may have

Database file size:

In [8]:
database_size = os.path.getsize(sqlite_file) / 1000000
print("The size of the database is: %s mb" %round(database_size, 2))

The size of the database is: 77.13 mb


Create my own function for rendering a database query into a pandas dataframe:

In [9]:
import pandas as pd
pd.set_option('display.max_rows', 6)
def df_query(query):
    df = pd.read_sql(query, conn)
    return df

Top 10 contributors:

In [10]:
query = """
SELECT
    all_tables.user,
    SUM(Total) Total
FROM
    (
    SELECT
        nodes.user,
        COUNT(*) AS Total
    FROM nodes
    GROUP BY nodes.user

    UNION ALL

    SELECT
        relations.user,
        COUNT(*) AS Total
    FROM relations
    GROUP BY relations.user
    
    UNION ALL
    
    SELECT
        ways.user,
        COUNT(*) AS Total
    FROM ways
    GROUP BY ways.user
    ORDER BY Total DESC   
    
    ) AS all_tables

GROUP BY user
ORDER BY Total DESC
LIMIT 10
"""

df_query(query)

user  Total
0     Matt Toups  25243
1   Maarten Deen  17221
2        Andre68   4370
..           ...    ...
7           wvdp    455
8         eric22    367
9         DKNOTT    201

[10 rows x 2 columns]

Total number of nodes, ways, relations:

In [11]:
# nodes
query = """
SELECT COUNT(*) AS Total FROM nodes
"""

df_query(query)

Total
0      2

In [12]:
# ways
query = """
SELECT COUNT(*) AS Total FROM ways
"""

df_query(query)

Total
0  53562

In [13]:
# relations
query = """
SELECT COUNT(*) AS Total FROM relations
"""

df_query(query)

Total
0    406

In [14]:
# nodes, ways and relations
query = """
SELECT
    SUM(all_tables.Total) AS Total_All
FROM 
    (
        SELECT COUNT(*) AS Total FROM nodes

        UNION ALL

        SELECT COUNT(*) AS Total FROM ways

        UNION ALL

        SELECT COUNT(*) AS Total FROM relations
    ) AS all_tables
"""

df_query(query)

Total_All
0      53970

Unnamed features:
* Way ID: 43829974 connects to one of its nodes: 555906935 which has lat/lon coordinates lat="29.2658771" lon="-89.4146036". OpenStreetMaps shows those coordinates indeeed to be just some random natural feature [hEre](http://www.openstreetmap.org/search?query=29.2658771%2C%20-89.4146036#map=18/29.26588/-89.41460).

What about all of the unnamed features?
First, to review the named ones:

In [15]:
# List of named features
query = """

SELECT
    all_tables.value
FROM
    (
    SELECT
        nodes_tags.value
    FROM nodes_tags
    WHERE nodes_tags.key="name"
    GROUP BY nodes_tags.value
    
    UNION ALL
    
    SELECT
        ways_tags.value
    FROM ways_tags
    WHERE ways_tags.key="name"
    GROUP BY ways_tags.value
    
    UNION ALL
    
    SELECT
        relations_tags.value
    FROM relations_tags
    WHERE relations_tags.key="name"
    GROUP BY relations_tags.value
    ORDER BY relations_tags.value
    
    ) AS all_tables

GROUP BY all_tables.value
ORDER BY all_tables.value
"""

df_query(query)

value
0          Abita Creek
1          Abita River
2           Adema Pond
..                 ...
265        Yankee Pond
266       Yellow Bayou
267  Yellow Lake Bayou

[268 rows x 1 columns]

Number of unnamed natural features:

In [16]:
# All node/way/relation ids with 'FType' as their key
query = """
SELECT
    all_tables.value,
    COUNT(*) AS Total
FROM
    (
    SELECT
        nodes_tags.value
    FROM nodes_tags
    WHERE nodes_tags.key="FType"
    
    UNION ALL
    
    SELECT
        ways_tags.value
    FROM ways_tags
    WHERE ways_tags.key="FType"
    
    UNION ALL
    
    SELECT
        relations_tags.value
    FROM relations_tags
    WHERE relations_tags.key="FType"
    
    ) AS all_tables
GROUP BY all_tables.value
ORDER BY Total DESC
"""

df_query(query)

value  Total
0      LakePond  22278
1    SwampMarsh  16200
2   StreamRiver  12371
..          ...    ...
10         Gate      6
11     Pipeline      6
12         Wall      6

[13 rows x 2 columns]

Note cleaning that needs to be done here - circle back to data.py algo and adjust where necessary... or,this is not cleaning - just the best way to describe the data...

All features that are not already named

In [17]:
# list of FTYPEs that are not in the list of named features
query = """
SELECT *, COUNT(*) as Total
    FROM (
    SELECT
        all_tables.id,
        all_tables.value
    FROM
        (
        SELECT
            *
        FROM nodes_tags
        WHERE nodes_tags.key="FType"
        
        UNION ALL
        
        SELECT
            *
        FROM ways_tags
        WHERE ways_tags.key="FType"

        UNION ALL

        SELECT
            *
        FROM relations_tags
        WHERE relations_tags.key="FType"

        ) AS all_tables
    ) AS ftype_table
WHERE ftype_table.id NOT IN (
    SELECT
        all_tables.id
    FROM
        (
        SELECT
            *
        FROM nodes_tags
        WHERE nodes_tags.key="name"
        
        UNION ALL
        
        SELECT
            *
        FROM ways_tags
        WHERE ways_tags.key="name"

        UNION ALL

        SELECT
            *
        FROM relations_tags
        WHERE relations_tags.key="name"

        ) AS all_tables
)
GROUP By ftype_table.value
ORDER BY Total DESC
"""

df_query(query)

id         value  Total
0     7077413      LakePond  21686
1     7077411    SwampMarsh  16188
2     2313282   StreamRiver  11758
..        ...           ...    ...
10   43275245      Pipeline      6
11  368947130          Wall      6
12   97140992  Lock Chamber      5

[13 rows x 3 columns]

In [ ]:
conn.close()

### Consider how the data could be improved:

Investigate (programmatically) the date the data was uploaded, then compare to the date when the NHD switched over to the Permanent identifier

All elements where NHD:GNIS_ID has a duplicate value with gnis:feature_id:

In [18]:
query = """
SELECT
    x.id,
    x.key,
    x.value,
    y.key,
    y.value
FROM (
    SELECT
        *
    FROM nodes_tags
    WHERE nodes_tags.key="GNIS_ID"

    UNION ALL
    
    SELECT
        *
    FROM ways_tags
    WHERE ways_tags.key="GNIS_ID"

    UNION ALL
    
    SELECT
        *
    FROM relations_tags
    WHERE relations_tags.key="GNIS_ID"
) AS x
    JOIN (
    SELECT
    *
    FROM nodes_tags
    WHERE nodes_tags.key="feature_id"
    
    UNION ALL
    
    SELECT
    *
    FROM ways_tags
    WHERE ways_tags.key="feature_id"
    
    UNION ALL
    
    SELECT
    *
    FROM relations_tags
    WHERE relations_tags.key="feature_id"
    ) AS y
    ON x.id=y.id
WHERE x.value=y.value
"""

df_query(query)

id      key     value         key     value
0     558006771  GNIS_ID  00559711  feature_id  00559711
1    3301246063  GNIS_ID  00554877  feature_id  00554877
2      22516599  GNIS_ID  00538745  feature_id  00538745
..          ...      ...       ...         ...       ...
924     4626652  GNIS_ID  00532593  feature_id  00532593
925     4626653  GNIS_ID  00555004  feature_id  00555004
926     5380366  GNIS_ID  00532757  feature_id  00532757

[927 rows x 5 columns]

All elements where NHD:Permanent_ is duplicate value with NHD:ComID

In [19]:
query = """
SELECT
    x.id,
    x.key,
    x.value,
    y.key,
    y.value
FROM (
    SELECT
        *
    FROM nodes_tags
    WHERE nodes_tags.key="ComID"

    UNION ALL
    
    SELECT
        *
    FROM ways_tags
    WHERE ways_tags.key="ComID"

    UNION ALL
    
    SELECT
        *
    FROM relations_tags
    WHERE relations_tags.key="ComID"
) AS x
    JOIN (
    SELECT
    *
    FROM nodes_tags
    WHERE nodes_tags.key="Permanent_"
    
    UNION ALL
    
    SELECT
    *
    FROM ways_tags
    WHERE ways_tags.key="Permanent_"
    
    UNION ALL
    
    SELECT
    *
    FROM relations_tags
    WHERE relations_tags.key="Permanent_"
    ) AS y
    ON x.id=y.id
WHERE x.value=y.value
"""

df_query(query)

id    key      value         key      value
0     43239879  ComID  148751000  Permanent_  148751000
1     43244825  ComID  148750992  Permanent_  148750992
2     43246802  ComID  151098269  Permanent_  151098269
...        ...    ...        ...         ...        ...
1292   4493454  ComID  151099663  Permanent_  151099663
1293   4493455  ComID  151099653  Permanent_  151099653
1294   4493460  ComID  151097798  Permanent_  151097798

[1295 rows x 5 columns]

NHD:way_id duplicated with NHD:ComID

In [20]:
query = """
SELECT
    x.id,
    x.key,
    x.value,
    y.key,
    y.value
FROM (
    SELECT
        *
    FROM nodes_tags
    WHERE nodes_tags.key="ComID"

    UNION ALL
    
    SELECT
        *
    FROM ways_tags
    WHERE ways_tags.key="ComID"

    UNION ALL
    
    SELECT
        *
    FROM relations_tags
    WHERE relations_tags.key="ComID"
) AS x
    JOIN (
    SELECT
    *
    FROM nodes_tags
    WHERE nodes_tags.key="way_id"
    
    UNION ALL
    
    SELECT
    *
    FROM ways_tags
    WHERE ways_tags.key="way_id"
    
    UNION ALL
    
    SELECT
    *
    FROM relations_tags
    WHERE relations_tags.key="way_id"
    ) AS y
    ON x.id=y.id
WHERE x.value=y.value
"""

df_query(query)

id    key      value     key      value
0       41225956  ComID  139142734  way_id  139142734
1       41226082  ComID  139142736  way_id  139142736
2       43166285  ComID  148743907  way_id  148743907
...          ...    ...        ...     ...        ...
12980  481376674  ComID  148740191  way_id  148740191
12981  482476279  ComID  148740240  way_id  148740240
12982  482476281  ComID  148740240  way_id  148740240

[12983 rows x 5 columns]